In [1]:
import itertools
import numpy as np
import pandas as pd
from collections import Counter
from sklearn.preprocessing import LabelEncoder

In [2]:
names = range(2010, 2019)
df = [pd.read_csv(f'csvs/{name}.csv') for name in names]
df = pd.concat(df, ignore_index=True, copy=False)
df = df[~df['examiner_id'].isna()]
df['examiner_id'] = df['examiner_id'].astype(np.int32)
df['inventor_list'] =df['inventor_list'].apply(eval)
print(df.shape)
df.head()

(2762354, 7)


application_number                                              title  \
0            12745329                                PROCESS AND PRODUCT   
1            12658202  Stabilized pharmaceutical compositions contain...   
2            12746833  MEDICAL APPLIANCE WITH A CONNECTION AND DISCON...   
3            12843590                 SAWHORSE BRACKET SYSTEM AND METHOD   
4            12748977                    One Piece Hip and Ridge Shingle   

                                            abstract main_ipcr_label  \
0  Process for producing a chocolate or chocolate...         A23G150   
1  The present invention provides a pharmaceutica...       A61K31397   
2  A medical appliance including a medical instru...         A61B100   
3  Embodiments of sawhorse systems are shown and ...         B25H106   
4  The invention provides a one piece shingle for...         E04D120   

   filing_date  examiner_id                                      inventor_list  
0     20100907        95893  [Rumbaut|Luc Joseph Paul Antoine Marie|Lebbeke...  
1     20100203        70017  [Wakiyama|Naoki|Yokohama-shi||JP, Usui|Fusao|Y...  
2     20100825        94236                       [Mathieu|Nicolas|Ecully||FR]  
3     20100726        85438  [Johnson|Michael|Waterville|WA|US, Johnson|Phi...  
4     20100329        70726  [Ward|Bryan|Olathe|KS|US, Rosewall|Ray|Blue Sp...

In [3]:
# Shuffle
df = df.sample(frac=1, random_state=42, replace=False, ignore_index=True)

In [5]:
data = {}

## Labels

The International Patent Classification (IPC) system has 4 levels of categorization, which are as follows:

1. Section: There are 8 main sections, represented by the letters A to H (e.g., Section A, Section B, etc.), each covering a broad field of technology.
2. Class: Each section is subdivided into multiple classes, typically represented by two-digit numbers. For example, A01 refers to agriculture; B01 refers to apparatus for physical or chemical processes.
3. Subclass: Each class is further divided into subclasses, which are denoted by three-digit numbers. For example, A01B refers to agricultural machines; B01D refers to separation processes.
4. Group: Subclasses are further divided into groups, typically indicated by more detailed numeric codes. These groups provide a more precise classification of specific technological aspects. For example, A01B1 refers to a specific type of agricultural machinery.

Summary:

- Section → Class → Subclass → Group

Each level progresses from broad categories to more specific and detailed classifications, enabling a precise and organized system for patent description and retrieval.

In [6]:
# We use level 2. (e.g., A01, B01,...)
labels = df['main_ipcr_label'].str[:3]
label_counts = df['main_ipcr_label'].str[:3].value_counts()
label_counts.tail(8)

main_ipcr_label
D07    183
C14    135
B82     64
B33     57
G12     39
H99      2
F99      1
E99      1
Name: count, dtype: int64

In [7]:
# Select labels with counts >= 100
min_counts = 100
labels_deleted = label_counts[label_counts >= min_counts].index
df = df[labels.isin(labels_deleted)]
df.shape

(2762187, 7)

In [8]:
df.loc[:, 'label'] = df['main_ipcr_label'].str[:3]

In [9]:
label_encoder = LabelEncoder()
labels = label_encoder.fit_transform(df['label'])
print('Number of classes', len(label_encoder.classes_))

Number of classes 120


In [10]:
labels = labels.astype(np.int8)

In [11]:
data['patent_labels'] = labels

## Patent-Examiner Links

In [12]:
patent_ids = np.arange(df.shape[0])

In [13]:
examiner_id_encoder = LabelEncoder()
examiner_ids = examiner_id_encoder.fit_transform(df['examiner_id'])
examiner_ids.max()+1

np.int64(10641)

In [14]:
examiner_ids = examiner_ids.astype(np.int16)

In [15]:
print('Number of patent-examiner links:', examiner_ids.shape[0])

Number of patent-examiner links: 2762187


In [16]:
data['patent-examiner'] = (patent_ids, examiner_ids)

## Patent-Inventor Links

In [17]:
df.loc[:, 'inventor_list'] = df['inventor_list'].apply(lambda xx: [x.lower() for x in xx])

In [18]:
inventors = list(itertools.chain(*(df['inventor_list'].values)))
inventor_count_dict = Counter(inventors)

In [19]:
inventor_count_df = pd.DataFrame(list(inventor_count_dict.items()), columns=['inventor', 'count'])
inventor_count_df.head()

inventor  count
0  bower|christopher|raleigh|nc|us     99
1      menard|etienne|limonges||fr      2
2       meitl|matthew|durham|nc|us    112
3    carr|joseph|chapel hill|nc|us     12
4        tsai|jui-yi|newtown|pa|us     33

In [20]:
inventor_count_df['count'].value_counts().head()

count
1    1683797
2     494218
3     224304
4     126584
5      79738
Name: count, dtype: int64

In [21]:
# Select inventors with at least 2 patents
selected_inventors = inventor_count_df['inventor'][inventor_count_df['count']>=2].values

In [22]:
inventor_id_encoder_all = LabelEncoder()
inventor_ids_all = inventor_id_encoder_all.fit_transform(inventors)
patent_ids_all = np.concatenate([np.full(count, i) 
                                 for i, count in enumerate(df['inventor_list'].apply(len))])
selected_inventor_ids = inventor_id_encoder_all.transform(selected_inventors)
masks = np.isin(inventor_ids_all, selected_inventor_ids) 

In [23]:
inventor_ids = inventor_ids_all[masks].astype(np.int32)
patent_ids = patent_ids_all[masks]
print('Number of patent-inventor links:', len(inventor_ids))

Number of patent-inventor links: 6071805


In [24]:
data['patent-inventor'] = (patent_ids, inventor_ids)

In [29]:
patent_years = (df['filing_date'] // 10000).values.astype(np.int16)
data['patent_years'] = patent_years

In [30]:
data

{'patent_labels': array([115,  56,  11, ..., 115,  58,  51], dtype=int8),
 'patent-examiner': (array([      0,       1,       2, ..., 2762184, 2762185, 2762186]),
  array([5875, 1162, 5676, ..., 6876, 5808, 7515], dtype=int16)),
 'patent-inventor': (array([      0,       0,       0, ..., 2762184, 2762185, 2762186]),
  array([ 218391, 1633817, 1630717, ..., 2301356,  766552, 1247700],
        dtype=int32)),
 'patent_years': array([2016, 2011, 2011, ..., 2016, 2016, 2016], dtype=int16)}

In [ ]:
import pickle

with open('patent.pkl', 'wb') as f:
    pickle.dump(data, f)

In [32]:
df.to_csv('Patent.csv', index=False)

### Node Features

We generate embeddings as features for each node in the graph. Node embeddings are generated by passing the title and the abstract through a Sentence-BERT model and obtaining a 384-embedding vector for each movie node.


According to [Sentence-Transformers docs](https://www.sbert.net/docs/pretrained_models.html), the **all-MiniLM-L6-v2** model provides the best quality. So we use it to generate node features.

all-MiniLM-L6-v2

Description:	All-round model tuned for many use-cases. Trained on a large and diverse dataset of over 1 billion training pairs.
Base Model:	nreimers/MiniLM-L6-H384-uncased
Max Sequence Length:	256
Dimensions:	384
Normalized Embeddings:	true
Suitable Score Functions:	dot-product (util.dot_score), cosine-similarity (util.cos_sim), euclidean distance
Size:	80 MB
Pooling:	Mean Pooling
Training Data:	1B+ training pairs. For details, see model card.
Model Card:	https://huggingface.co/sentence-transformers/all-MiniLM-L6-v2


In [1]:
import pandas as pd

df = pd.read_csv('Patent.csv')
df.head()

application_number                                              title  \
0            15243228  METHODS OF FORMING PRINTABLE INTEGRATED CIRCUI...   
1            13033229      RUTHENIUM CARBENE COMPLEXES FOR OLED MATERIAL   
2            13218612                                         BED INSERT   
3            13828921  IMAGE DISPLAY APPARATUS AND METHOD FOR OPERATI...   
4            15373712                     BI-DIRECTIONAL ROLLER ASSEMBLY   

                                            abstract main_ipcr_label  \
0  Methods of forming integrated circuit devices ...        H01L2712   
1  Neutral ruthenium(II) complexes having at leas...        C07F1500   
2  An insert for a bed facilitates use of a mattr...        A47C2100   
3  An image display apparatus and a method for op...         G06F301   
4  Disclosed is a method of assembling a roller a...         F16L318   

   filing_date  examiner_id  \
0     20160822        75592   
1     20110223        60315   
2     20110826        74819   
3     20130314        66365   
4     20161209        58099   

                                       inventor_list label  
0  ['bower|christopher|raleigh|nc|us', 'menard|et...   H01  
1                      ['tsai|jui-yi|newtown|pa|us']   C07  
2                  ["o'reagan|james r.|greer|sc|us"]   A47  
3  ['choi|eunjung|seoul||kr', 'choi|kwangsoo|seou...   G06  
4                    ['costa|carlos|somerset|ma|us']   F16

In [3]:
import pickle

with open('patent.pkl', 'rb') as f:
    data = pickle.load(f)
data

{'patent_labels': array([115,  56,  11, ..., 115,  58,  51], dtype=int8),
 'patent-examiner': (array([      0,       1,       2, ..., 2762184, 2762185, 2762186]),
  array([5875, 1162, 5676, ..., 6876, 5808, 7515], dtype=int16)),
 'patent-inventor': (array([      0,       0,       0, ..., 2762184, 2762185, 2762186]),
  array([ 218391, 1633817, 1630717, ..., 2301356,  766552, 1247700],
        dtype=int32)),
 'patent_years': array([2016, 2011, 2011, ..., 2016, 2016, 2016], dtype=int16)}

In [4]:
import torch
from sentence_transformers import SentenceTransformer

device = 'cuda:0' if torch.cuda.is_available() else 'cpu'
model = SentenceTransformer('../sentence-transformers/all-MiniLM-L6-v2', device=device)
model

/usr/local/lib/python3.10/dist-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


SentenceTransformer(
  (0): Transformer({'max_seq_length': 256, 'do_lower_case': False}) with Transformer model: BertModel 
  (1): Pooling({'word_embedding_dimension': 384, 'pooling_mode_cls_token': False, 'pooling_mode_mean_tokens': True, 'pooling_mode_max_tokens': False, 'pooling_mode_mean_sqrt_len_tokens': False, 'pooling_mode_weightedmean_tokens': False, 'pooling_mode_lasttoken': False, 'include_prompt': True})
  (2): Normalize()
)

In [5]:
text = df['title'] + ' ' + df['abstract']

In [18]:
feats = model.encode(text, batch_size=4096, show_progress_bar=True, convert_to_numpy=True)

Batches: 100%|██████████| 675/675 [33:12<00:00,  2.95s/it]


In [22]:
data['patent_feats'] = feats

In [25]:
with open('patent.pkl', 'wb') as f:
    pickle.dump(data, f)